# Measurements with the combined probe head

The combined probe head (ball-pen probe + Langmuir probe) offers measurements of the plasma potential $\Phi$, floating potential $V_{fl}$ and electron temperature $T_e$ with high temporal resolution (1 $\mu$s). In this notebook, its data is loaded, processed and plotted.

Before that, let's load some basic modules: numpy (for basic operations with arrays), pandas (for storing signals) and pylab (for plotting).

In [ ]:
# Import basic modules
import numpy as np
import pandas as pd
import pylab as plt
from matplotlib import rc,rcParams
rc('font', weight='bold')
plt.rcParams['axes.labelweight'] = 'bold'

## Basic data access

To access the GOLEM data, we write the function `get_data`.

In [ ]:
def get_data(name, shot):
    '''Return data of given diagnostic name in given shot.'''
    data = pd.read_csv(f'http://golem.fjfi.cvut.cz/shots/{shot}/DASs/PetiProbe/{name}.csv', names = ['t','data'])
    data.t = data.t*1000
    data = data.set_index('t')
    return data

To test `get_data`, we load the data of tunnel probe oriented toward limiter from the current discharge. The signal is called `1-Lim`.

In [ ]:
shot = 0
data = get_data('1-Lim', shot)
data.head()

The data has two components: a time axis given in seconds and the voltage collected at that time. Let's plot the time evolution $V_{fl}(t)$.

In [ ]:
ax = data.plot()
ax.set_xlabel('t [ms]')

The interesting part of this plot is between roughly 0 ms and 15 ms. Using these time limits, we can replot the $V_{fl}(t)$ graph. 

In [ ]:
t1,t2 = [0, 15]
ax = data.loc[t1:t2].plot()
ax.set_xlabel('t [ms]')

## Offset removal

An offset is a non-physical contribution to the signal, created by parasitic voltages, cross-talk between diagnostics, electronic noise and many other influences. In the simplest case, an offset is constant during the tokamak discharge. We can then calculate the offset by averaging our collected data during a time where they are supposed to be zero (typically before the discharge) and then subtract this value from the entire signal.

Typically probe voltages do show offsets, as demonstrated in the following.

In [ ]:
ax = data[:0.5].plot()
ax.set_xlabel('t [ms]')

At the time $t=5$ ms ($t=0$ ms is globally the time when the data acquisition system starts recording diagnostic signals) the discharge is procedure is initiated. Since the sampling frequency is 1 MHz (distance 1 $\mu$s between individual voltage samples), we average the voltage in the first 500 samples (0.5 ms) to calculate the offset.

In [ ]:
offset = data[:0.5].mean()
data = data - offset
ax = data[:0.5].plot()
ax.set_xlabel('t [ms]')

## Electron temperature calculation

To measure the electron temperature $T_e$, both the ball-pen probe and the Langmuir probe must be so-called *floating*. This means that they are electrically insulated from their surroundings and we measure the voltage which the plasma particles will charge them to. This *floating voltage* is different for both probes due to their different design. The ball-pen probe floating voltage is

$V_{BPP} = \Phi - 0.3T_e$

where $\Phi$ is the plasma potential, and the Langmuir probe floating voltage is

$V_{fl} = \Phi - 2.8T_e$.

It then follows that the electron temperature can be calculated by subtracting the two floating voltages:

$T_e = \dfrac{V_{BPP}-V_{LP}}{2.5}.$

In the following, both the probe signals are loaded and visualised to show that the ball-pen probe floating voltage is, indeed, higher than the Langmuir probe floating voltage.

In [ ]:
# Load the signals
V_BPP = get_data('3-BPP', shot)*100
V_fl = get_data('4-LP', shot)*100

# Remove offsets
V_BPP -= V_BPP[:0.5].mean()
V_fl -= V_fl[:0.5].mean()


# Plot the signals
ax1=V_BPP.loc[t1:t2].plot()
ax1.legend(['BPP'])
ax1.set_xlabel('t [ms]')
ax1.set_ylabel('U [V]')
ax2=V_fl.loc[t1:t2].plot()
ax2.legend(['LP'])
ax1.set_xlabel('t [ms]')
ax2.set_ylabel('U [V]')

We then calculate the electron temperature by subtracting the two signals.

In [ ]:
Te = (V_BPP-V_fl)/2.5
ax = Te.loc[t1:t2].plot()
ax.set_xlabel('t [ms]')
ax.set_ylabel(r'$T_\mathrm{e}$ [eV]')
ax.legend([r'$T_\mathrm{e}$'])
plt.savefig('icon-fig.jpg')

In [ ]:
from scipy import signal

## Mach number calculation:

$M = \frac{1}{4} \ln(\frac{TP_\mathrm{olim}}{TP_\mathrm{lim}})$


In [ ]:
Lim = get_data('1-Lim', shot).rolling(50).mean()
#Lim.data = signal.savgol_filter(Lim.data,101,1)
oLim = get_data('2-OLim', shot).rolling(50).mean()
#oLim.data = signal.savgol_filter(oLim.data,101,1)

In [ ]:
Mpar = 0.25*np.log(oLim/Lim)
Mpar.loc[t1:t2].plot()